# 安装环境

In [ ]:
!apt-get install git
# 安装 Node.js 的 LTS 版本
!curl -fsSL https://deb.nodesource.com/setup_lts.x | sudo -E bash -
# 添加go的源
!add-apt-repository ppa:longsleep/golang-backports -y
!apt-get update
!apt-get install -y nodejs
!apt-get install -y golang-go
!apt install npm
!npm install -g pnpm
!apt install build-essential

In [ ]:
!node -v
!go version

# 克隆代码

In [ ]:
!git clone https://github.com/alist-org/alist.git
!git clone --recurse-submodules https://github.com/alist-org/alist-web.git

# 下载语言文件

In [ ]:
!cd alist-web && wget https://crowdin.com/backend/download/project/alist/zh-CN.zip && unzip zh-CN.zip
!cd alist-web && node ./scripts/i18n.mjs
!cd alist-web && rm zh-CN.zip

# 在修改完后安装项目所有依赖，同时编译前端文件

In [ ]:
#把淘宝源修改为官方源
!cd alist-web && sed -i 's/registry\.npm\.taobao\.org/registry.npmjs.org/g' pnpm-lock.yaml
!cd alist-web && pnpm install && pnpm run build

# 编译后端

In [ ]:
# 移动前端编译的dist至后端
!cp -r /content/alist-web/dist /content/alist/public/

## Linux_AMD64

修改完之后运行以下代码，进行后端编译

In [ ]:
%%bash

# 进入 alist 文件夹
cd alist

# 创建 Shell 脚本
cat <<EOL > build_alist.sh
#!/bin/bash

appName="alist"
builtAt="\$(date +'%F %T %z')"
goVersion=\$(go version | sed 's/go version //')
gitAuthor=\$(git show -s --format='format:%aN <%ae>' HEAD)
gitCommit=\$(git log --pretty=format:"%h" -1)
version=\$(git describe --long --tags --dirty --always)
webVersion=\$(wget -qO- -t1 -T2 "https://api.github.com/repos/alist-org/alist-web/releases/latest" | grep "tag_name" | head -n 1 | awk -F ":" '{print \$2}' | sed 's/\"//g;s/,//g;s/ //g')
ldflags="\
-w -s \
-X 'github.com/alist-org/alist/v3/internal/conf.BuiltAt=\$builtAt' \
-X 'github.com/alist-org/alist/v3/internal/conf.GoVersion=\$goVersion' \
-X 'github.com/alist-org/alist/v3/internal/conf.GitAuthor=\$gitAuthor' \
-X 'github.com/alist-org/alist/v3/internal/conf.GitCommit=\$gitCommit' \
-X 'github.com/alist-org/alist/v3/internal/conf.Version=\$version' \
-X 'github.com/alist-org/alist/v3/internal/conf.WebVersion=\$webVersion' \
"
go build -ldflags="\$ldflags -linkmode external -extldflags -static" .
EOL

In [ ]:
# 添加执行权限并运行 Shell 脚本
!cd alist && bash build_alist.sh

In [ ]:
# 压缩二进制
!apt install upx -y
!cd alist && upx --ultra-brute alist -o alist2

In [ ]:
# 安装ngrok
%%bash
curl -s https://ngrok-agent.s3.amazonaws.com/ngrok.asc \
  | sudo tee /etc/apt/trusted.gpg.d/ngrok.asc >/dev/null && echo "deb https://ngrok-agent.s3.amazonaws.com buster main" \
  | sudo tee /etc/apt/sources.list.d/ngrok.list && sudo apt update && sudo apt install ngrok

In [ ]:
# 添加ngrok的token

token = input("Your ngrok token: ")
!ngrok config add-authtoken $token

In [ ]:
# 测试是否能正常运行
import secrets, json, re, pathlib

get_ipython().system_raw("ngrok http 5244 &")
!sleep 1
tunnels = !curl -s http://localhost:4040/api/tunnels
url = json.loads(tunnels[0])['tunnels'][0]['public_url']
!curl -s http://localhost:4040/api/tunnels | python3 -c "import sys, json; print(json.load(sys.stdin)['tunnels'][0]['public_url'])"
!cd alist && ./alist admin random && ./alist server

## Linux_ARM64

修改完之后运行以下代码，进行后端编译

In [ ]:
# 安装ARM需要的环境
!apt install gcc-aarch64-linux-gnu g++-aarch64-linux-gnu -y
# 安装go-sqlite3
!cd alist && go get github.com/mattn/go-sqlite3

In [ ]:
%%bash

# 进入 alist 文件夹
cd alist

# 创建 Shell 脚本
cat <<EOL > build_alist_arm64.sh
#!/bin/bash

# 交叉编译-arm64
export GOOS=linux
export GOARCH=arm64
export GOARM=7
export CGO_ENABLED=1
export CC=aarch64-linux-gnu-gcc
export CXX=aarch64-linux-gnu-g++
export AR=aarch64-linux-gnu-ar

appName="alist"
builtAt="\$(date +'%F %T %z')"
goVersion=\$(go version | sed 's/go version //')
gitAuthor=\$(git show -s --format='format:%aN <%ae>' HEAD)
gitCommit=\$(git log --pretty=format:"%h" -1)
version=\$(git describe --long --tags --dirty --always)
webVersion=\$(wget -qO- -t1 -T2 "https://api.github.com/repos/alist-org/alist-web/releases/latest" | grep "tag_name" | head -n 1 | awk -F ":" '{print \$2}' | sed 's/\"//g;s/,//g;s/ //g')
ldflags="\
-w -s \
-X 'github.com/alist-org/alist/v3/internal/conf.BuiltAt=\$builtAt' \
-X 'github.com/alist-org/alist/v3/internal/conf.GoVersion=\$goVersion' \
-X 'github.com/alist-org/alist/v3/internal/conf.GitAuthor=\$gitAuthor' \
-X 'github.com/alist-org/alist/v3/internal/conf.GitCommit=\$gitCommit' \
-X 'github.com/alist-org/alist/v3/internal/conf.Version=\$version' \
-X 'github.com/alist-org/alist/v3/internal/conf.WebVersion=\$webVersion' \
"
go build -ldflags="\$ldflags -linkmode external -extldflags -static" .
EOL

In [ ]:
# 添加执行权限并运行 Shell 脚本
!cd alist && bash build_alist_arm64.sh

## Windows_amd64

In [ ]:
# 安装环境
!apt-get install gcc-mingw-w64-x86-64 g++-mingw-w64-x86-64 -y
# 安装go-sqlite3
!cd alist && go get github.com/mattn/go-sqlite3

修改完成之后运行以下代码，进行编译

In [ ]:
%%bash

# 进入 alist 文件夹
cd alist

# 创建 Shell 脚本
cat <<EOL > build_alist_win64.sh
#!/bin/bash
# 交叉编译-win64
export CC=x86_64-w64-mingw32-gcc
export CXX=x86_64-w64-mingw32-g++
export CGO_ENABLED=1
export GOOS=windows
export GOARCH=amd64

appName="alist"
builtAt="\$(date +'%F %T %z')"
goVersion=\$(go version | sed 's/go version //')
gitAuthor=\$(git show -s --format='format:%aN <%ae>' HEAD)
gitCommit=\$(git log --pretty=format:"%h" -1)
version=\$(git describe --long --tags --dirty --always)
webVersion=\$(wget -qO- -t1 -T2 "https://api.github.com/repos/alist-org/alist-web/releases/latest" | grep "tag_name" | head -n 1 | awk -F ":" '{print \$2}' | sed 's/\"//g;s/,//g;s/ //g')
ldflags="\
-w -s \
-X 'github.com/alist-org/alist/v3/internal/conf.BuiltAt=\$builtAt' \
-X 'github.com/alist-org/alist/v3/internal/conf.GoVersion=\$goVersion' \
-X 'github.com/alist-org/alist/v3/internal/conf.GitAuthor=\$gitAuthor' \
-X 'github.com/alist-org/alist/v3/internal/conf.GitCommit=\$gitCommit' \
-X 'github.com/alist-org/alist/v3/internal/conf.Version=\$version' \
-X 'github.com/alist-org/alist/v3/internal/conf.WebVersion=\$webVersion' \
"
go build -ldflags="\$ldflags -linkmode external -extldflags -static" .
EOL

In [ ]:
# 添加执行权限并运行 Shell 脚本
!cd alist && bash build_alist_win64.sh

# 上传修改编译好的`alist`至`Google Drive`

In [ ]:
# 挂载网盘
from google.colab import drive

drive.mount('/content/drive')

In [ ]:
# 上传
!cp "/content/alist/alist" "/content/drive/MyDrive/ownbackup/alist"